In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import sqlite3
import zipfile
import scipy.stats as st
import math
from wordcloud import WordCloud, STOPWORDS
from datetime import datetime
from xgboost import XGBRegressor
from sklearn.model_selection import train_test_split
import scipy.stats as stats
from sklearn.preprocessing import StandardScaler
import xgboost as xgb
from sklearn.metrics import r2_score
from xgboost import plot_importance
from sklearn.utils import resample
from sklearn import metrics
from sklearn.tree import DecisionTreeRegressor

# suppress futurewarnings from statistical packages
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

import matplotlib.ticker as mticker
from tabulate import tabulate
import plotly
import plotly.express as px

plotly.offline.init_notebook_mode()
#read data

zip_file = "../Dataset/AB_US_2020.zip"
try:
    with zipfile.ZipFile(zip_file, 'r') as z:
        z.extractall("Dataset/unZipped/")
        print("Extracted all")
except:
    print("Invalid file")
    
airbnbDS = pd.read_csv("Dataset/unZipped/AB_US_2020.csv")

#Going to drop neighbourhood_group because of have the values are null. 
#For both name and host name I will fill the empty slots with "N/A", 
#there is very few missing and I do not think name will be very important to regesion on price. 
#For all null values in reviews_per_month will be replaced with 0. 
#For all last review that are null will be replaced with "00/00/00"


airbnbDS = airbnbDS.drop("neighbourhood_group", axis = 1)


airbnbDS = airbnbDS.fillna(value= {'name': 'N/A', 'host_name':'N/A', 'reviews_per_month': 0})

airbnbDS = airbnbDS.dropna()

room_ID_dic = {'Entire home/apt': 1, 'Private room': 2,'Shared room': 3, 'Hotel room': 4}

airbnbDS['room_type_ID'] = airbnbDS['room_type'].apply(lambda x: room_ID_dic[x])

city_ID_dic = {'Asheville' : 1, 'Austin' : 2, 'Boston' :3, 'Broward County' :4, 'Cambridge':5,
       'Chicago':6, 'Clark County':7, 'Columbus':8, 'Denver':9, 'Hawaii':10,
       'Jersey City':11, 'Los Angeles':12, 'Nashville':13, 'New Orleans':14,
       'New York City':15, 'Oakland':16, 'Pacific Grove':17, 'Portland':18,
       'Rhode Island':19, 'Salem':20, 'San Clara Country':21, 'San Diego':22,
       'San Francisco':23, 'San Mateo County':24, 'Santa Cruz County':25,
       'Seattle':26, 'Twin Cities MSA':27, 'Washington D.C.':28}


airbnbDS['city_ID'] = airbnbDS['city'].apply(lambda x: city_ID_dic[x])

airbnbDS['last_review'] = pd.to_datetime(airbnbDS['last_review'])

airbnbDS['days_since_last_review'] = datetime.now() - airbnbDS['last_review']

airbnbDS['days_since_last_review'] = airbnbDS['days_since_last_review'].dt.days



Extracted all


C:\Users\clineman\Anaconda3\envs\learn-env\lib\site-packages\IPython\core\interactiveshell.py:3145: DtypeWarning:

Columns (4) have mixed types.Specify dtype option on import or set low_memory=False.



In [2]:
airbnbDS.describe()

id       host_id       latitude      longitude  \
count  1.774280e+05  1.774280e+05  177428.000000  177428.000000   
mean   2.349823e+07  8.449619e+07      35.728741    -103.247427   
std    1.263624e+07  9.067049e+07       6.789461      25.967295   
min    1.090000e+02  2.300000e+01      18.920990    -159.714900   
25%    1.368938e+07  1.212612e+07      32.770550    -121.570070   
50%    2.338574e+07  4.673526e+07      37.259625    -104.874350   
75%    3.446794e+07  1.339236e+08      40.722143     -76.987305   
max    4.549250e+07  3.679176e+08      47.734620     -70.995950   

               price  minimum_nights  number_of_reviews  reviews_per_month  \
count  177428.000000    1.774280e+05      177428.000000       177428.00000   
mean      184.520188    5.723698e+02          43.958738            1.43145   
std       430.596928    2.374045e+05          68.832735            1.68321   
min         0.000000    1.000000e+00           1.000000            0.01000   
25%        75.000000    1.000000e+00           4.000000            0.23000   
50%       116.000000    2.000000e+00          16.000000            0.81000   
75%       195.000000    5.000000e+00          54.000000            2.06000   
max     24999.000000    1.000000e+08         966.000000           44.06000   

       calculated_host_listings_count  availability_365   room_type_ID  \
count                   177428.000000     177428.000000  177428.000000   
mean                        11.391404        157.951518       1.343029   
std                         33.375799        138.129585       0.552196   
min                          1.000000          0.000000       1.000000   
25%                          1.000000          1.000000       1.000000   
50%                          2.000000        139.000000       1.000000   
75%                          5.000000        305.000000       2.000000   
max                        393.000000        365.000000       4.000000   

             city_ID  days_since_last_review  
count  177428.000000           177428.000000  
mean       14.056958             1160.717311  
std         6.873973              402.127897  
min         1.000000              758.000000  
25%        10.000000              911.000000  
50%        14.000000             1029.000000  
75%        18.000000             1222.000000  
max        28.000000             4667.000000

## Dummy variables

In [3]:
airbnbDS.dtypes

id                                         int64
name                                      object
host_id                                    int64
host_name                                 object
neighbourhood                             object
latitude                                 float64
longitude                                float64
room_type                                 object
price                                      int64
minimum_nights                             int64
number_of_reviews                          int64
last_review                       datetime64[ns]
reviews_per_month                        float64
calculated_host_listings_count             int64
availability_365                           int64
city                                      object
room_type_ID                               int64
city_ID                                    int64
days_since_last_review                     int64
dtype: object

In [4]:
modelDS = airbnbDS.copy()
modelRF = airbnbDS.copy()

In [5]:
modelRF

id                                               name  \
0          38585    Charming Victorian home - twin beds + breakfast   
1          80905                                   French Chic Loft   
2         108061  Walk to stores/parks/downtown. Fenced yard/Pet...   
3         155305                 Cottage! BonPaul + Sharky's Hostel   
4         160594                                Historic Grove Park   
...          ...                                                ...   
225936  45326130      Modern and cozy home located in Washington DC   
225950  45349877  Penthouse w/ Patio ‚òÜ Capitol Hill Condo ‚òÜ ...   
225955  45352724  MODERN ‚òÜ Well-Located Shaw Town Home ‚òÜ 2BR...   
225964  45385834      Brand new modern apartment with private entry   
226002  45472150  LUXE 1-BR STUDIO SPACE / Desirable Location + ...   

          host_id  host_name  \
0          165529    Evelyne   
1          427027    Celeste   
2          320564       Lisa   
3          746673    BonPaul   
4          769252  Elizabeth   
...           ...        ...   
225936   55489711       Amir   
225950    3850096        Ije   
225955    3850096        Ije   
225964   16561471     Victor   
226002  367917574       Tara   

                                            neighbourhood  latitude  \
0                                                   28804  35.65146   
1                                                   28801  35.59779   
2                                                   28801  35.60670   
3                                                   28806  35.57864   
4                                                   28801  35.61442   
...                                                   ...       ...   
225936          Union Station, Stanton Park, Kingman Park  38.90101   
225950                         Capitol Hill, Lincoln Park  38.88703   
225955     Howard University, Le Droit Park, Cardozo/Shaw  38.91626   
225964               Brightwood Park, Crestwood, Petworth  38.94358   
226002  Edgewood, Bloomingdale, Truxton Circle, Eckington  38.91457   

        longitude        room_type  price  minimum_nights  number_of_reviews  \
0       -82.62792     Private room     60               1                138   
1       -82.55540  Entire home/apt    470               1                114   
2       -82.55563  Entire home/apt     75              30                 89   
3       -82.59578  Entire home/apt     90               1                267   
4       -82.54127     Private room    125              30                 58   
...           ...              ...    ...             ...                ...   
225936  -77.00283  Entire home/apt    144               1                  1   
225950  -77.00586  Entire home/apt    132               2                  1   
225955  -77.02074  Entire home/apt    112               2                  1   
225964  -77.01283  Entire home/apt     78               1                  1   
226002  -77.00911  Entire home/apt     76               1                  1   

       last_review  reviews_per_month  calculated_host_listings_count  \
0       2020-02-16               1.14                               1   
1       2020-07-09               1.03                              11   
2       2019-11-30               0.81                               2   
3       2020-09-22               2.39                               5   
4       2015-10-19               0.52                               1   
...            ...                ...                             ...   
225936  2020-09-18               1.00                               1   
225950  2020-09-16               1.00                               8   
225955  2020-09-13               1.00                               8   
225964  2020-09-19               1.00                               1   
226002  2020-09-18               1.00                               1   

        availability_365             city  room_type_ID  city_ID  \
0                

removing the columns that we will not use in the model

In [6]:
modelDS = modelDS.drop('id', axis =1)
modelDS = modelDS.drop('name', axis =1)
modelDS = modelDS.drop('host_id', axis =1)
modelDS = modelDS.drop('host_name', axis =1)
modelDS = modelDS.drop('neighbourhood', axis =1)
modelDS = modelDS.drop('room_type', axis =1)
modelDS = modelDS.drop('city', axis =1)
modelDS = modelDS.drop('last_review', axis =1)

modelRF = modelRF.drop('id', axis =1)
modelRF = modelRF.drop('name', axis =1)
modelRF = modelRF.drop('host_id', axis =1)
modelRF = modelRF.drop('host_name', axis =1)
modelRF = modelRF.drop('neighbourhood', axis =1)
modelRF = modelRF.drop('room_type', axis =1)
modelRF = modelRF.drop('city', axis =1)
modelRF = modelRF.drop('last_review', axis =1)

In [7]:
modelDS

latitude  longitude  price  minimum_nights  number_of_reviews  \
0       35.65146  -82.62792     60               1                138   
1       35.59779  -82.55540    470               1                114   
2       35.60670  -82.55563     75              30                 89   
3       35.57864  -82.59578     90               1                267   
4       35.61442  -82.54127    125              30                 58   
...          ...        ...    ...             ...                ...   
225936  38.90101  -77.00283    144               1                  1   
225950  38.88703  -77.00586    132               2                  1   
225955  38.91626  -77.02074    112               2                  1   
225964  38.94358  -77.01283     78               1                  1   
226002  38.91457  -77.00911     76               1                  1   

        reviews_per_month  calculated_host_listings_count  availability_365  \
0                    1.14                               1                 0   
1                    1.03                              11               288   
2                    0.81                               2               298   
3                    2.39                               5                 0   
4                    0.52                               1                 0   
...                   ...                             ...               ...   
225936               1.00                               1               328   
225950               1.00                               8               162   
225955               1.00                               8               171   
225964               1.00                               1                75   
226002               1.00                               1               173   

        room_type_ID  city_ID  days_since_last_review  
0                  2        1                    1055  
1                  1        1                     911  
2                  1        1                    1133  
3                  1        1                     836  
4                  2        1                    2636  
...              ...      ...                     ...  
225936             1       28                     840  
225950             1       28                     842  
225955             1       28                     845  
225964             1       28                     839  
226002             1       28                     840  

[177428 rows x 11 columns]

In [8]:
modelDS.corr()

latitude  longitude     price  minimum_nights  \
latitude                        1.000000   0.558152 -0.058386        0.000711   
longitude                       0.558152   1.000000 -0.049598       -0.001756   
price                          -0.058386  -0.049598  1.000000       -0.000642   
minimum_nights                  0.000711  -0.001756 -0.000642        1.000000   
number_of_reviews               0.050037  -0.040210 -0.060874       -0.001247   
reviews_per_month               0.053906  -0.021908 -0.055226       -0.001790   
calculated_host_listings_count -0.203682  -0.213236  0.076714       -0.000738   
availability_365               -0.177410  -0.148488  0.047300       -0.002710   
room_type_ID                    0.138919   0.112847 -0.122937        0.002822   
city_ID                         0.448815  -0.046814 -0.004054        0.003087   
days_since_last_review          0.119590   0.126213  0.002119        0.005172   

                                number_of_reviews  reviews_per_month  \
latitude                                 0.050037           0.053906   
longitude                               -0.040210          -0.021908   
price                                   -0.060874          -0.055226   
minimum_nights                          -0.001247          -0.001790   
number_of_reviews                        1.000000           0.732273   
reviews_per_month                        0.732273           1.000000   
calculated_host_listings_count          -0.113825          -0.113099   
availability_365                         0.068520           0.043291   
room_type_ID                            -0.039671          -0.074901   
city_ID                                  0.040011           0.007045   
days_since_last_review                  -0.255399          -0.389714   

                                calculated_host_listings_count  \
latitude                                             -0.203682   
longitude                                            -0.213236   
price                                                 0.076714   
minimum_nights                                       -0.000738   
number_of_reviews                                    -0.113825   
reviews_per_month                                    -0.113099   
calculated_host_listings_count                        1.000000   
availability_365                                      0.132094   
room_type_ID                                         -0.089915   
city_ID                                              -0.032374   
days_since_last_review                               -0.047839   

                                availability_365  room_type_ID   city_ID  \
latitude                               -0.177410      0.138919  0.448815   
longitude                              -0.148488      0.112847 -0.046814   
price                                   0.047300     -0.122937 -0.004054   
minimum_nights                         -0.002710      0.002822  0.003087   
number_of_reviews                       0.068520     -0.039671  0.040011   
reviews_per_month                       0.043291     -0.074901  0.007045   
calculated_host_listings_count          0.132094     -0.089915 -0.032374   
availability_365                        1.000000     -0.025836 -0.081520   
room_type_ID                           -0.025836      1.000000  0.053049   
city_ID                                -0.081520      0.053049  1.000000   
days_since_last_review                 -0.241980      0.088162  0.067814   

                                days_since_last_review  
latitude                                      0.119590  
longitude                                     0.126213  
price                                         0.002119  
minimum_nights                                0.005172  
number_of_reviews                            -0.255399  
reviews_per_month                            -0.389714  
calculated_host_listings_count               -0.047839  
availability_365                

#  Removing Outliers

In [9]:
# Removing outliers
lower_bound = .0
upper_bound = .95
modelDS = modelDS[modelDS['price'].between(modelDS['price'].quantile(lower_bound), \
            modelDS['price'].quantile(upper_bound), inclusive=True)].reset_index(drop=True)
modelRF = modelRF[modelRF['price'].between(modelRF['price'].quantile(lower_bound), \
            modelRF['price'].quantile(upper_bound), inclusive=True)].reset_index(drop=True)

In [10]:
modelDS.describe()

latitude      longitude          price  minimum_nights  \
count  168601.000000  168601.000000  168601.000000    1.686010e+05   
mean       35.821908    -102.948702     136.768293    6.019266e+02   
std         6.761705      25.924187      90.523192    2.435398e+05   
min        18.920990    -159.711430       0.000000    1.000000e+00   
25%        32.787190    -118.769200      71.000000    1.000000e+00   
50%        37.327550     -97.846830     110.000000    2.000000e+00   
75%        40.723330     -74.105750     176.000000    5.000000e+00   
max        47.734620     -70.995950     485.000000    1.000000e+08   

       number_of_reviews  reviews_per_month  calculated_host_listings_count  \
count      168601.000000      168601.000000                   168601.000000   
mean           45.184495           1.463621                       11.049662   
std            69.986867           1.703096                       32.938092   
min             1.000000           0.010000                        1.000000   
25%             4.000000           0.240000                        1.000000   
50%            17.000000           0.840000                        2.000000   
75%            56.000000           2.120000                        5.000000   
max           966.000000          44.060000                      393.000000   

       availability_365   room_type_ID        city_ID  days_since_last_review  
count     168601.000000  168601.000000  168601.000000           168601.000000  
mean         155.483651       1.356243      14.070777             1159.384529  
std          137.842529       0.556009       6.845154              401.778559  
min            0.000000       1.000000       1.000000              758.000000  
25%            0.000000       1.000000      10.000000              911.000000  
50%          133.000000       1.000000      14.000000             1029.000000  
75%          301.000000       2.000000      18.000000             1214.000000  
max          365.000000       4.000000      28.000000             4667.000000

In [11]:
modelDS.corr()

latitude  longitude     price  minimum_nights  \
latitude                        1.000000   0.553455 -0.156597        0.000698   
longitude                       0.553455   1.000000 -0.128875       -0.001832   
price                          -0.156597  -0.128875  1.000000       -0.001853   
minimum_nights                  0.000698  -0.001832 -0.001853        1.000000   
number_of_reviews               0.044832  -0.047516 -0.092055       -0.001300   
reviews_per_month               0.047590  -0.030031 -0.105320       -0.001861   
calculated_host_listings_count -0.195017  -0.208212  0.119947       -0.000741   
availability_365               -0.178087  -0.150665  0.101042       -0.002742   
room_type_ID                    0.137515   0.110958 -0.395118        0.002817   
city_ID                         0.445939  -0.049406 -0.023344        0.003175   
days_since_last_review          0.122307   0.130379 -0.009797        0.005318   

                                number_of_reviews  reviews_per_month  \
latitude                                 0.044832           0.047590   
longitude                               -0.047516          -0.030031   
price                                   -0.092055          -0.105320   
minimum_nights                          -0.001300          -0.001861   
number_of_reviews                        1.000000           0.732630   
reviews_per_month                        0.732630           1.000000   
calculated_host_listings_count          -0.111611          -0.110781   
availability_365                         0.076069           0.051196   
room_type_ID                            -0.048729          -0.085957   
city_ID                                  0.041066           0.007297   
days_since_last_review                  -0.257506          -0.391760   

                                calculated_host_listings_count  \
latitude                                             -0.195017   
longitude                                            -0.208212   
price                                                 0.119947   
minimum_nights                                       -0.000741   
number_of_reviews                                    -0.111611   
reviews_per_month                                    -0.110781   
calculated_host_listings_count                        1.000000   
availability_365                                      0.132991   
room_type_ID                                         -0.089823   
city_ID                                              -0.032554   
days_since_last_review                               -0.048561   

                                availability_365  room_type_ID   city_ID  \
latitude                               -0.178087      0.137515  0.445939   
longitude                              -0.150665      0.110958 -0.049406   
price                                   0.101042     -0.395118 -0.023344   
minimum_nights                         -0.002742      0.002817  0.003175   
number_of_reviews                       0.076069     -0.048729  0.041066   
reviews_per_month                       0.051196     -0.085957  0.007297   
calculated_host_listings_count          0.132991     -0.089823 -0.032554   
availability_365                        1.000000     -0.017648 -0.080806   
room_type_ID                           -0.017648      1.000000  0.054731   
city_ID                                -0.080806      0.054731  1.000000   
days_since_last_review                 -0.249476      0.090986  0.067646   

                                days_since_last_review  
latitude                                      0.122307  
longitude                                     0.130379  
price                                        -0.009797  
minimum_nights                                0.005318  
number_of_reviews                            -0.257506  
reviews_per_month                            -0.391760  
calculated_host_listings_count               -0.048561  
availability_365                

In [12]:
modelDS.shape

(168601, 11)

#  Model

In [13]:
modelDS

latitude  longitude  price  minimum_nights  number_of_reviews  \
0       35.65146  -82.62792     60               1                138   
1       35.59779  -82.55540    470               1                114   
2       35.60670  -82.55563     75              30                 89   
3       35.57864  -82.59578     90               1                267   
4       35.61442  -82.54127    125              30                 58   
...          ...        ...    ...             ...                ...   
168596  38.90101  -77.00283    144               1                  1   
168597  38.88703  -77.00586    132               2                  1   
168598  38.91626  -77.02074    112               2                  1   
168599  38.94358  -77.01283     78               1                  1   
168600  38.91457  -77.00911     76               1                  1   

        reviews_per_month  calculated_host_listings_count  availability_365  \
0                    1.14                               1                 0   
1                    1.03                              11               288   
2                    0.81                               2               298   
3                    2.39                               5                 0   
4                    0.52                               1                 0   
...                   ...                             ...               ...   
168596               1.00                               1               328   
168597               1.00                               8               162   
168598               1.00                               8               171   
168599               1.00                               1                75   
168600               1.00                               1               173   

        room_type_ID  city_ID  days_since_last_review  
0                  2        1                    1055  
1                  1        1                     911  
2                  1        1                    1133  
3                  1        1                     836  
4                  2        1                    2636  
...              ...      ...                     ...  
168596             1       28                     840  
168597             1       28                     842  
168598             1       28                     845  
168599             1       28                     839  
168600             1       28                     840  

[168601 rows x 11 columns]

In [14]:
X = modelDS.drop('price', axis = 1)
y = modelDS['price']

scaler = StandardScaler()
X =scaler.fit_transform(X)

X = np.array(X)
y = np.array(y)

In [15]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 20)

X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size = 0.2, random_state =20 )

In [16]:
dtrain = xgb.DMatrix(X_train, label = y_train)
dval = xgb.DMatrix(X_val, label = y_val)
dtest = xgb.DMatrix(X_test, label = y_test)

In [ ]:
params = {'learning_rate': 0.001, 'max_depth':6}
model = xgb.train(params, dtrain,evals=[(dval, 'eval')], num_boost_round = 100000, early_stopping_rounds = 10)

[0]	eval-rmse:163.01579
Will train until eval-rmse hasn't improved in 10 rounds.
[1]	eval-rmse:162.88762
[2]	eval-rmse:162.75937
[3]	eval-rmse:162.63141
[4]	eval-rmse:162.50368
[5]	eval-rmse:162.37604
[6]	eval-rmse:162.24838
[7]	eval-rmse:162.12111
[8]	eval-rmse:161.99385
[9]	eval-rmse:161.86676
[10]	eval-rmse:161.73988
[11]	eval-rmse:161.61304
[12]	eval-rmse:161.48656
[13]	eval-rmse:161.35983
[14]	eval-rmse:161.23384
[15]	eval-rmse:161.10767
[16]	eval-rmse:160.98158
[17]	eval-rmse:160.85584
[18]	eval-rmse:160.73013
[19]	eval-rmse:160.60461
[20]	eval-rmse:160.47905
[21]	eval-rmse:160.35408
[22]	eval-rmse:160.22894
[23]	eval-rmse:160.10400
[24]	eval-rmse:159.97916
[25]	eval-rmse:159.85463
[26]	eval-rmse:159.73018
[27]	eval-rmse:159.60593
[28]	eval-rmse:159.48163
[29]	eval-rmse:159.35776
[30]	eval-rmse:159.23395
[31]	eval-rmse:159.11020
[32]	eval-rmse:158.98671
[33]	eval-rmse:158.86327
[34]	eval-rmse:158.74002
[35]	eval-rmse:158.61694
[36]	eval-rmse:158.49399
[37]	eval-rmse:158.37132
[38

[318]	eval-rmse:129.31317
[319]	eval-rmse:129.22745
[320]	eval-rmse:129.14156
[321]	eval-rmse:129.05598
[322]	eval-rmse:128.97070
[323]	eval-rmse:128.88542
[324]	eval-rmse:128.80022
[325]	eval-rmse:128.71495
[326]	eval-rmse:128.62975
[327]	eval-rmse:128.54468
[328]	eval-rmse:128.45995
[329]	eval-rmse:128.37538
[330]	eval-rmse:128.29077
[331]	eval-rmse:128.20615
[332]	eval-rmse:128.12189
[333]	eval-rmse:128.03775
[334]	eval-rmse:127.95348
[335]	eval-rmse:127.86951
[336]	eval-rmse:127.78574
[337]	eval-rmse:127.70197
[338]	eval-rmse:127.61807
[339]	eval-rmse:127.53445
[340]	eval-rmse:127.45104
[341]	eval-rmse:127.36774
[342]	eval-rmse:127.28445
[343]	eval-rmse:127.20142
[344]	eval-rmse:127.11827
[345]	eval-rmse:127.03556
[346]	eval-rmse:126.95292
[347]	eval-rmse:126.86994
[348]	eval-rmse:126.78736
[349]	eval-rmse:126.70505
[350]	eval-rmse:126.62246
[351]	eval-rmse:126.54037
[352]	eval-rmse:126.45830
[353]	eval-rmse:126.37642
[354]	eval-rmse:126.29428
[355]	eval-rmse:126.21252
[356]	eval-r

[634]	eval-rmse:107.25768
[635]	eval-rmse:107.20221
[636]	eval-rmse:107.14690
[637]	eval-rmse:107.09164
[638]	eval-rmse:107.03647
[639]	eval-rmse:106.98113
[640]	eval-rmse:106.92616
[641]	eval-rmse:106.87132
[642]	eval-rmse:106.81641
[643]	eval-rmse:106.76177
[644]	eval-rmse:106.70718
[645]	eval-rmse:106.65256
[646]	eval-rmse:106.59771
[647]	eval-rmse:106.54333
[648]	eval-rmse:106.48901
[649]	eval-rmse:106.43475
[650]	eval-rmse:106.38026
[651]	eval-rmse:106.32614
[652]	eval-rmse:106.27219
[653]	eval-rmse:106.21791
[654]	eval-rmse:106.16406
[655]	eval-rmse:106.11008
[656]	eval-rmse:106.05631
[657]	eval-rmse:106.00279
[658]	eval-rmse:105.94930
[659]	eval-rmse:105.89590
[660]	eval-rmse:105.84251
[661]	eval-rmse:105.78922
[662]	eval-rmse:105.73566
[663]	eval-rmse:105.68253
[664]	eval-rmse:105.62949
[665]	eval-rmse:105.57621
[666]	eval-rmse:105.52329
[667]	eval-rmse:105.47051
[668]	eval-rmse:105.41766
[669]	eval-rmse:105.36472
[670]	eval-rmse:105.31214
[671]	eval-rmse:105.25958
[672]	eval-r

[956]	eval-rmse:93.06377
[957]	eval-rmse:93.02978
[958]	eval-rmse:92.99535
[959]	eval-rmse:92.96164
[960]	eval-rmse:92.92776
[961]	eval-rmse:92.89344
[962]	eval-rmse:92.85988
[963]	eval-rmse:92.82630
[964]	eval-rmse:92.79214
[965]	eval-rmse:92.75878
[966]	eval-rmse:92.72529
[967]	eval-rmse:92.69160
[968]	eval-rmse:92.65847
[969]	eval-rmse:92.62472
[970]	eval-rmse:92.59130
[971]	eval-rmse:92.55826
[972]	eval-rmse:92.52472
[973]	eval-rmse:92.49119
[974]	eval-rmse:92.45821
[975]	eval-rmse:92.42501
[976]	eval-rmse:92.39208
[977]	eval-rmse:92.35934
[978]	eval-rmse:92.32642
[979]	eval-rmse:92.29312
[980]	eval-rmse:92.26052
[981]	eval-rmse:92.22782
[982]	eval-rmse:92.19463
[983]	eval-rmse:92.16226
[984]	eval-rmse:92.12966
[985]	eval-rmse:92.09699
[986]	eval-rmse:92.06480
[987]	eval-rmse:92.03237
[988]	eval-rmse:91.99997
[989]	eval-rmse:91.96799
[990]	eval-rmse:91.93526
[991]	eval-rmse:91.90304
[992]	eval-rmse:91.87106
[993]	eval-rmse:91.83863
[994]	eval-rmse:91.80679
[995]	eval-rmse:91.77477


[1273]	eval-rmse:84.60238
[1274]	eval-rmse:84.58157
[1275]	eval-rmse:84.56130
[1276]	eval-rmse:84.54103
[1277]	eval-rmse:84.52108
[1278]	eval-rmse:84.50090
[1279]	eval-rmse:84.48077
[1280]	eval-rmse:84.46085
[1281]	eval-rmse:84.44077
[1282]	eval-rmse:84.42079
[1283]	eval-rmse:84.40102
[1284]	eval-rmse:84.38110
[1285]	eval-rmse:84.36108
[1286]	eval-rmse:84.34140
[1287]	eval-rmse:84.32162
[1288]	eval-rmse:84.30177
[1289]	eval-rmse:84.28209
[1290]	eval-rmse:84.26250
[1291]	eval-rmse:84.24282
[1292]	eval-rmse:84.22312
[1293]	eval-rmse:84.20348
[1294]	eval-rmse:84.18411
[1295]	eval-rmse:84.16460
[1296]	eval-rmse:84.14427
[1297]	eval-rmse:84.12477
[1298]	eval-rmse:84.10535
[1299]	eval-rmse:84.08597
[1300]	eval-rmse:84.06657
[1301]	eval-rmse:84.04742
[1302]	eval-rmse:84.02810
[1303]	eval-rmse:84.00884
[1304]	eval-rmse:83.98959
[1305]	eval-rmse:83.97036
[1306]	eval-rmse:83.95106
[1307]	eval-rmse:83.93205
[1308]	eval-rmse:83.91296
[1309]	eval-rmse:83.89398
[1310]	eval-rmse:83.87495
[1311]	eval-

...

[25012]	eval-rmse:68.02034
[25013]	eval-rmse:68.02032
[25014]	eval-rmse:68.02030
[25015]	eval-rmse:68.02029
[25016]	eval-rmse:68.02022
[25017]	eval-rmse:68.02016
[25018]	eval-rmse:68.02002
[25019]	eval-rmse:68.01997
[25020]	eval-rmse:68.01992
[25021]	eval-rmse:68.01981
[25022]	eval-rmse:68.01973
[25023]	eval-rmse:68.01961
[25024]	eval-rmse:68.01939
[25025]	eval-rmse:68.01917
[25026]	eval-rmse:68.01917
[25027]	eval-rmse:68.01916
[25028]	eval-rmse:68.01913
[25029]	eval-rmse:68.01904
[25030]	eval-rmse:68.01904
[25031]	eval-rmse:68.01896
[25032]	eval-rmse:68.01894
[25033]	eval-rmse:68.01887
[25034]	eval-rmse:68.01879
[25035]	eval-rmse:68.01875
[25036]	eval-rmse:68.01872
[25037]	eval-rmse:68.01872
[25038]	eval-rmse:68.01864
[25039]	eval-rmse:68.01862
[25040]	eval-rmse:68.01831
[25041]	eval-rmse:68.01815
[25042]	eval-rmse:68.01808
[25043]	eval-rmse:68.01807
[25044]	eval-rmse:68.01797
[25045]	eval-rmse:68.01799
[25046]	eval-rmse:68.01798
[25047]	eval-rmse:68.01797
[25048]	eval-rmse:68.01797
[

[25316]	eval-rmse:67.99864
[25317]	eval-rmse:67.99861
[25318]	eval-rmse:67.99860
[25319]	eval-rmse:67.99858
[25320]	eval-rmse:67.99861
[25321]	eval-rmse:67.99860
[25322]	eval-rmse:67.99831
[25323]	eval-rmse:67.99831
[25324]	eval-rmse:67.99832
[25325]	eval-rmse:67.99831
[25326]	eval-rmse:67.99811
[25327]	eval-rmse:67.99806
[25328]	eval-rmse:67.99799
[25329]	eval-rmse:67.99787
[25330]	eval-rmse:67.99780
[25331]	eval-rmse:67.99774
[25332]	eval-rmse:67.99774
[25333]	eval-rmse:67.99771
[25334]	eval-rmse:67.99766
[25335]	eval-rmse:67.99767
[25336]	eval-rmse:67.99768
[25337]	eval-rmse:67.99754
[25338]	eval-rmse:67.99738
[25339]	eval-rmse:67.99736
[25340]	eval-rmse:67.99725
[25341]	eval-rmse:67.99723
[25342]	eval-rmse:67.99721
[25343]	eval-rmse:67.99710
[25344]	eval-rmse:67.99701
[25345]	eval-rmse:67.99699
[25346]	eval-rmse:67.99696
[25347]	eval-rmse:67.99695
[25348]	eval-rmse:67.99695
[25349]	eval-rmse:67.99695
[25350]	eval-rmse:67.99687
[25351]	eval-rmse:67.99677
[25352]	eval-rmse:67.99674
[

[25620]	eval-rmse:67.98224
[25621]	eval-rmse:67.98220
[25622]	eval-rmse:67.98217
[25623]	eval-rmse:67.98214
[25624]	eval-rmse:67.98209
[25625]	eval-rmse:67.98209
[25626]	eval-rmse:67.98208
[25627]	eval-rmse:67.98209
[25628]	eval-rmse:67.98208
[25629]	eval-rmse:67.98202
[25630]	eval-rmse:67.98199
[25631]	eval-rmse:67.98197
[25632]	eval-rmse:67.98198
[25633]	eval-rmse:67.98184
[25634]	eval-rmse:67.98173
[25635]	eval-rmse:67.98171
[25636]	eval-rmse:67.98158
[25637]	eval-rmse:67.98151
[25638]	eval-rmse:67.98148
[25639]	eval-rmse:67.98134
[25640]	eval-rmse:67.98126
[25641]	eval-rmse:67.98116
[25642]	eval-rmse:67.98110
[25643]	eval-rmse:67.98109
[25644]	eval-rmse:67.98095
[25645]	eval-rmse:67.98094
[25646]	eval-rmse:67.98093
[25647]	eval-rmse:67.98092
[25648]	eval-rmse:67.98090
[25649]	eval-rmse:67.98080
[25650]	eval-rmse:67.98070
[25651]	eval-rmse:67.98064
[25652]	eval-rmse:67.98055
[25653]	eval-rmse:67.98041
[25654]	eval-rmse:67.98030
[25655]	eval-rmse:67.98024
[25656]	eval-rmse:67.98022
[

[25924]	eval-rmse:67.96658
[25925]	eval-rmse:67.96659
[25926]	eval-rmse:67.96659
[25927]	eval-rmse:67.96658
[25928]	eval-rmse:67.96651
[25929]	eval-rmse:67.96648
[25930]	eval-rmse:67.96641
[25931]	eval-rmse:67.96639
[25932]	eval-rmse:67.96639
[25933]	eval-rmse:67.96641
[25934]	eval-rmse:67.96635
[25935]	eval-rmse:67.96621
[25936]	eval-rmse:67.96615
[25937]	eval-rmse:67.96606
[25938]	eval-rmse:67.96607
[25939]	eval-rmse:67.96609
[25940]	eval-rmse:67.96606
[25941]	eval-rmse:67.96586
[25942]	eval-rmse:67.96584
[25943]	eval-rmse:67.96584
[25944]	eval-rmse:67.96582
[25945]	eval-rmse:67.96577
[25946]	eval-rmse:67.96570
[25947]	eval-rmse:67.96564
[25948]	eval-rmse:67.96564
[25949]	eval-rmse:67.96554
[25950]	eval-rmse:67.96542
[25951]	eval-rmse:67.96536
[25952]	eval-rmse:67.96532
[25953]	eval-rmse:67.96519
[25954]	eval-rmse:67.96513
[25955]	eval-rmse:67.96510
[25956]	eval-rmse:67.96512
[25957]	eval-rmse:67.96503
[25958]	eval-rmse:67.96487
[25959]	eval-rmse:67.96487
[25960]	eval-rmse:67.96489
[

[26228]	eval-rmse:67.95100
[26229]	eval-rmse:67.95100
[26230]	eval-rmse:67.95100
[26231]	eval-rmse:67.95094
[26232]	eval-rmse:67.95094
[26233]	eval-rmse:67.95092
[26234]	eval-rmse:67.95087
[26235]	eval-rmse:67.95082
[26236]	eval-rmse:67.95074
[26237]	eval-rmse:67.95068
[26238]	eval-rmse:67.95057
[26239]	eval-rmse:67.95057
[26240]	eval-rmse:67.95053
[26241]	eval-rmse:67.95048
[26242]	eval-rmse:67.95048
[26243]	eval-rmse:67.95049
[26244]	eval-rmse:67.95048
[26245]	eval-rmse:67.95040
[26246]	eval-rmse:67.95039
[26247]	eval-rmse:67.95029
[26248]	eval-rmse:67.95021
[26249]	eval-rmse:67.95013
[26250]	eval-rmse:67.95002
[26251]	eval-rmse:67.94971
[26252]	eval-rmse:67.94965
[26253]	eval-rmse:67.94955
[26254]	eval-rmse:67.94939
[26255]	eval-rmse:67.94926
[26256]	eval-rmse:67.94916
[26257]	eval-rmse:67.94913
[26258]	eval-rmse:67.94911
[26259]	eval-rmse:67.94910
[26260]	eval-rmse:67.94902
[26261]	eval-rmse:67.94900
[26262]	eval-rmse:67.94891
[26263]	eval-rmse:67.94891
[26264]	eval-rmse:67.94884
[

In [ ]:
xgModel = XGBRegressor()
xgModel.fit(X_train, y_train)
xgModel.score(X_test,y_test)

In [ ]:
from sklearn.metrics import mean_squared_error
from math import sqrt
y_true = np.array(y_test, dtype=np.float64)
y_pred = np.array(model.predict(dtest), dtype=np.float64)
print("R^2 Score: {:.4f}" .format(r2_score(y_true, y_pred)))
print("MSE Score: {:.4f}" .format(mean_squared_error(y_true, y_pred)))
print("RMSE Score: {:.4f}" .format(sqrt(mean_squared_error(y_true, y_pred))))

In [ ]:
plt.figure(figsize=(20,8))
sns.residplot(x=y_test[:1000],y=y_pred[:1000])

In [ ]:
d=y_pred-y_test

plt.hist(d, bins=100)

In [ ]:
xgb.plot_importance(model, ax=plt.gca())
plt.show()

Second Model

Decision Tree

In [ ]:
X = modelRF.drop('price', axis = 1)
y = modelRF['price']

scaler = StandardScaler()
X =scaler.fit_transform(X)

X = np.array(X)
y = np.array(y)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 20)

X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size = 0.2, random_state =20 )

In [ ]:
rf_model = DecisionTreeRegressor()
rf_model.fit(X_train,y_train)
rf_model.score(X_test,y_test)

In [ ]:
y_true = np.array(y_test, dtype=np.float64)


print("MSE Score: {:.4f}" .format(mean_squared_error(y_true, y_train)))
print("RMSE Score: {:.4f}" .format(sqrt(mean_squared_error(y_true, y_train))))

In [ ]:
from sklearn.tree import plot_tree
plt.figure(figsize = (25,10))
plot_tree(rf_model)
plt.title("decision tree", fontsize = 25)

 

plt.show()

In [ ]:
xgModel = DecisionTreeRegressor()
xgModel.fit(X_train, y_train)
xgModel.score(X_test,y_test)

In [ ]:
from sklearn.metrics import mean_squared_error


In [ ]:
from xgboost import XGBClassifier
model = XGBClassifier(learning_rate=.1)
model.fit(X_train, y_train)
y_pred = model.predict(X_test)
print("Accuracy:",metrics.accuracy_score(y_test, y_pred))
print("Precision:",metrics.precision_score(y_test, y_pred, average = none))
print("Recall:",metrics.recall_score(y_test, y_pred))
print("fbeta:",metrics.fbeta_score(y_test, y_pred, average='weighted', beta=0.5))

In [ ]:
plot_importance(model, max_num_features=10, importance_type ='gain')
plt.rcParams['figure.figsize'] = (40,10)
plt.show()

removing all columns with low correlation (under 10%)

In [ ]:
#modelDS.corr()

In [ ]:
# modelDS = modelDS.drop('number_of_reviews', axis =1)
# modelDS = modelDS.drop('calculated_host_listings_count', axis =1)

In [ ]:
# X = modelDS.drop('price', axis = 1)
# y = modelDS['price']

# scaler = StandardScaler()
# X =scaler.fit_transform(X)

# X = np.array(X)
# y = np.array(y)

# X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 20)

# X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size = 0.2, random_state =20 )

# xgModel = XGBRegressor()
# xgModel.fit(X_train, y_train)
# xgModel.score(X_test,y_test)

In [ ]:
# xgModel = XGBRegressor()
# xgModel.fit(X_train, y_train)
# xgModel.score(X_test,y_test)

In [ ]:
# dtrain = xgb.DMatrix(X_train, label = y_train)
# dval = xgb.DMatrix(X_val, label = y_val)
# dtest = xgb.DMatrix(X_test, label = y_test)

In [ ]:
# params = {'learning_rate': 0.001, 'max_depth':6}
# model = xgb.train(params, dtrain,evals=[(dval, 'eval')], num_boost_round = 10000, early_stopping_rounds = 10)

In [ ]:
# y_true = np.array(y_test, dtype=np.float64)
# y_pred = np.array(model.predict(dtest), dtype=np.float64)
# print("R^2 Score: {:.4f}" .format(r2_score(y_true, y_pred)))

In [ ]:
# from sklearn import metrics

# print('MAE:', metrics.mean_absolute_error(y_test, predictions).round(2))
# print('MSE:', metrics.mean_squared_error(y_test, predictions).round(2))
# print('RMSE:', np.sqrt(metrics.mean_squared_error(y_test, predictions)).round(2))